In [1]:
import pandas as pd
import geopandas as gpd
import math

In [2]:
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

# Your first interactive map

### Several arguments customize the appearance of the map:
- location : 지도의 센터 설정
    - [37.541 ,  126.986]  # 서울시 좌표
    - [42.32  , -71.0589]  # 보스턴 좌표
- tiles : 맵 스타일
    - oepnstreetmap, Stamenterrain,  Stamentoner, Stamenwatercolor 등
- zoom_start : 값이 클수록 지도를 더 가깝게 

In [3]:
# Create a map
m_1 = folium.Map(location=[42.32,-71.0589], tiles='openstreetmap', zoom_start=10)

# Display the map
m_1

# The DATA

In [4]:
import os
b_path = 'C:\\Users\\user\\Desktop\\data\\geopd'
crime_path = os.path.join(b_path, 'crimes-in-boston/crimes-in-boston/crime.csv')
# Load the data
crimes = pd.read_csv(crime_path, encoding='latin-1')

# Drop rows with missing locations
crimes.dropna(subset=['Lat', 'Long', 'DISTRICT'], inplace=True)

# Focus on major crimes in 2018
crimes = crimes[crimes.OFFENSE_CODE_GROUP.isin([
    'Larceny', 'Auto Theft', 'Robbery', 'Larceny From Motor Vehicle', 'Residential Burglary',
    'Simple Assault', 'Harassment', 'Ballistics', 'Aggravated Assault', 'Other Burglary', 
    'Arson', 'Commercial Burglary', 'HOME INVASION', 'Homicide', 'Criminal Harassment', 
    'Manslaughter'])]
crimes = crimes[crimes.YEAR>=2018]

# Print the first five rows of the table
crimes.head()

INCIDENT_NUMBER  OFFENSE_CODE          OFFENSE_CODE_GROUP  \
0       I182070945           619                     Larceny   
6       I182070933           724                  Auto Theft   
8       I182070931           301                     Robbery   
19      I182070915           614  Larceny From Motor Vehicle   
24      I182070908           522        Residential Burglary   

                      OFFENSE_DESCRIPTION DISTRICT REPORTING_AREA SHOOTING  \
0                      LARCENY ALL OTHERS      D14            808      NaN   
6                              AUTO THEFT       B2            330      NaN   
8                        ROBBERY - STREET       C6            177      NaN   
19  LARCENY THEFT FROM MV - NON-ACCESSORY       B2            181      NaN   
24      BURGLARY - RESIDENTIAL - NO FORCE       B2            911      NaN   

       OCCURRED_ON_DATE  YEAR  MONTH DAY_OF_WEEK  HOUR  UCR_PART  \
0   2018-09-02 13:00:00  2018      9      Sunday    13  Part One   
6   2018-09-03 21:25:00  2018      9      Monday    21  Part One   
8   2018-09-03 20:48:00  2018      9      Monday    20  Part One   
19  2018-09-02 18:00:00  2018      9      Sunday    18  Part One   
24  2018-09-03 18:38:00  2018      9      Monday    18  Part One   

               STREET        Lat       Long                     Location  
0          LINCOLN ST  42.357791 -71.139371  (42.35779134, -71.13937053)  
6         NORMANDY ST  42.306072 -71.082733  (42.30607218, -71.08273260)  
8   MASSACHUSETTS AVE  42.331521 -71.070853  (42.33152148, -71.07085307)  
19         SHIRLEY ST  42.325695 -71.068168  (42.32569490, -71.06816778)  
24    ANNUNCIATION RD  42.335062 -71.093168  (42.33506218, -71.09316781)

In [5]:
daytime_robberies = crimes[((crimes.OFFENSE_CODE_GROUP == 'Robbery') & \
                            (crimes.HOUR.isin(range(9,18))))]

In [6]:
# Create a map
m_2 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

# Add points to the map
for idx, row in daytime_robberies.iterrows():
    Marker([row['Lat'], row['Long']]).add_to(m_2)

# Display the map
m_2

# folium.plugins.MarkerCluster

- 추가할 마커가 많은 경우 folium.plugins.MarkerCluster()를 사용하여 클러스터로 저장

In [7]:
# Create the map
m_3 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

# Add points to the map
mc = MarkerCluster()
for idx, row in daytime_robberies.iterrows():
    if not math.isnan(row['Long']) and not math.isnan(row['Lat']):
        mc.add_child(Marker([row['Lat'], row['Long']]))
m_3.add_child(mc)

# Display the map
m_3

# Bubble Maps

- location : 원의 중심 설정
- radius : 원 반경 설정
    - 전통적인 Bubble 맵에서는 함수를 정의하여(마치 color_producer()와 같은) 크기를 다양하게 조절할 수 있음
    - 특정 요인의 대소에 따라 크기를 다르게 할 수 있다
- The color_producer()

In [9]:
# Create a base map
m_4 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)
def color_producer(val):
    if val <= 12:
        return 'forestgreen'
    else:
        return 'darkred'

# Add a bubble map to the base map
for i in range(0,len(daytime_robberies)):
    Circle(
        location=[daytime_robberies.iloc[i]['Lat'], daytime_robberies.iloc[i]['Long']],
        radius=20,
        color=color_producer(daytime_robberies.iloc[i]['HOUR'])).add_to(m_4)

# Display the map
m_4

### radius 조작 코드
- Course와 상관없음
- 시간의 크기에 따라 원의 크기 조절

In [11]:
# Create a base map
m_4 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)
def color_producer(val):
    if val <= 12:
        return 'forestgreen'
    else:
        return 'darkred'

# Add a bubble map to the base map
for i in range(0,len(daytime_robberies)):
    Circle(
        location=[daytime_robberies.iloc[i]['Lat'], daytime_robberies.iloc[i]['Long']],
        radius=int(daytime_robberies.iloc[i]['HOUR'])*10,
        color=color_producer(daytime_robberies.iloc[i]['HOUR'])).add_to(m_4)

# Display the map
m_4

# Heatmaps
- 특정 요인의 밀도 표현

- data : DataFrame형식의 좌표 데이터
- radius : 평활도 제어 / 값이 커질수록 더 간격이 좁아짐

In [12]:
# Create a base map
m_5 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a heatmap to the base map
HeatMap(data=crimes[['Lat', 'Long']], radius=10).add_to(m_5)

# Display the map
m_5

In [17]:
# Create a base map
m_5 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a heatmap to the base map
HeatMap(data=crimes[['Lat', 'Long']], radius=30).add_to(m_5)

# Display the map
m_5

# Choropleth maps

- 각 구역에 서로 다른 행이 할당되는 GeoDataFrame을 만들고 "기하학" 열에 지리적 경계가 포함됩니다.

In [18]:
# GeoDataFrame with geographical boundaries of Boston police districts
district_path = os.path.join(b_path, 'Police_Districts/Police_Districts/Police_Districts.shp')
districts_full = gpd.read_file(district_path)
districts = districts_full[["DISTRICT", "geometry"]].set_index("DISTRICT")
districts.head()

geometry
DISTRICT                                                   
A15       MULTIPOLYGON (((-71.07416 42.39051, -71.07415 ...
A7        MULTIPOLYGON (((-70.99644 42.39557, -70.99644 ...
A1        POLYGON ((-71.05200 42.36884, -71.05169 42.368...
C6        POLYGON ((-71.04406 42.35403, -71.04412 42.353...
D4        POLYGON ((-71.07416 42.35724, -71.07359 42.357...

In [19]:
# Number of crimes in each police district
plot_dict = crimes.DISTRICT.value_counts()
plot_dict.head()

D4     2885
B2     2231
A1     2130
C11    1899
B3     1421
Name: DISTRICT, dtype: int64

- geo_data : GeoJSON 데이터
    - 코드에서는 __geo_interface__ 속성을 사용하여 GeoDataFrame 구역을 GeoJSON FeatureCollection으로 변환함
- data : Pandas Series
- key_on : 항상 feature.id로 세팅
    - 이는 Geo_데이터에 사용되는 GeoDataFrame과 데이터에 제공되는 판다 시리즈의 인덱스가 동일하다는 사실을 의미
    - 자세한 내용을 이해하려면 GeoJSON 기능 모음의 구조를 파악해야 함
    - features 항목이 데이터를 포함하고 있으며, 항목 중 id 값을 포함
- fill_color : 색상표 조합
    - 컬러확인 : http://colorbrewer2.org/
    - 커스텀 : https://nbviewer.jupyter.org/github/python-visualization/folium/blob/v0.2.0/examples/Colormaps.ipynb
- legend_name : 오른쪽 상단에 표시될 라벨값

In [26]:
districts.__geo_interface__

{'type': 'FeatureCollection',
 'features': [{'id': 'A15',
   'type': 'Feature',
   'properties': {},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [(((-71.07415718153364, 42.390507686248306),
       (-71.07415424746895, 42.390503696137124),
       (-71.07403961352766, 42.39054086496418),
       (-71.07393964511492, 42.390379143356114),
       (-71.07377237566668, 42.39009698543054),
       (-71.07361166169, 42.389830761341194),
       (-71.07344403708477, 42.389546953156085),
       (-71.07326831318817, 42.38925652728944),
       (-71.0730937070298, 42.388965557003026),
       (-71.07292832121637, 42.38867983419289),
       (-71.07293103519046, 42.38866118498357),
       (-71.07283365981914, 42.38850029570664),
       (-71.07275606610709, 42.38836993909938),
       (-71.07268736490828, 42.38823796794029),
       (-71.0727338745498, 42.38814813477101),
       (-71.07272171746692, 42.388139034570465),
       (-71.07271618331094, 42.38814620998887),
       (-71.07271201154819

In [21]:
# Create a base map
m_6 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Major criminal incidents (Jan-Aug 2018)'
          ).add_to(m_6)

# Display the map
m_6